<pre>
Needs to be using python 2 kernal

python2 -m pip install ipykernel

python2 -m ipykernel install --usern

I added this to my .bashrc file

export SPARK_HOME=/home/andrew/Downloads/spark-2.1.0-bin-hadoop2.7
export PATH = $Spark_HOME/bin:$PATH


export PYTHONPATH=$SPARK_HOME/python/$PYTHONPATH
export PYTHONPATH=$SPARK_HOME/python/lib/py4j-0.10.4-src.zip$PYTHONPATH

Then finally

pip2 install findspark
</pre>

In [1]:
import findspark
findspark.init()
import pyspark
spark = pyspark.sql.SparkSession \
    .builder \
    .appName("Read Some Parquet") \
    .config("spark.some.config.option", "some-value") \
    .getOrCreate()

In [2]:

df = spark.read.parquet("/home/andrew/Documents/CAMCOS/Verizon/Verizon data/agg/oneday/feature/day=2016-11-25")
df.show()

+----------------+------------+-----------+-------+
|    subscriberid|featureValue|featureType|measure|
+----------------+------------+-----------+-------+
|3220237051000000|        dpcz|          4|    1.0|
|2294189755000000|       djud1|          4|    1.0|
|8102531227000000|       66413|          3|    1.0|
|5720868074000000|       57730|          3|    1.0|
|7931520141000000|       65746|          3|    1.0|
|4388889546000000|       dr77q|          4|    1.0|
|3684046523000000|       91750|          3|    1.0|
|8702309588000000|       80524|          3|    1.0|
|3506846389000000|       99502|          3|    1.0|
|6506852123000000|     9q5f36v|          4|    1.0|
|2777595771000000|       56320|          3|    1.0|
|5882619442000000|       dpq8r|          4|    1.0|
|3737765807000000|       99026|          3|    1.0|
|3754656122000000|       43964|          3|    1.0|
|2790677778000000|        9r94|          4|    1.0|
|7887428116000000|       70446|          3|    1.0|
|55395489980

In [3]:
df.createOrReplaceTempView("table1")
df2 = spark.sql("SELECT DISTINCT subscriberid from table1") 
print("There are ",df2.count(), "unique subscriberids and ", df.count(), " rows the original")

('There are ', 92527, 'unique subscriberids and ', 219873, ' rows the original')


In [4]:
df2 = spark.sql("SELECT DISTINCT featureValue from table1") 
print("There are ",df2.count(), "unique featureValues")

('There are ', 52652, 'unique featureValues')


<pre>
Now let's look at our hist table
</pre>

In [5]:
hist = spark.read.parquet("/home/andrew/Documents/CAMCOS/Verizon/Verizon data/agg/agg/hist/date=20170202")
hist.show()

+----------------+-------+--------------+----------+-----------+--------------------+--------------------+------------+-------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+----------------+--------------------+---------------+--------------------+--------------------+-------+--------------------+-------+-------------------+---------------------+-----------------+------+---------+---------+---------+-------------------+-------+---------+-----------------+----------+-----------+--------------+----------+----------------+----------+-------------------+---------------+----------------+-------------------+-----------------+---------------+--------------------------+------------------------+-----------------------------+------------------+-----------------------------+-------------------+------------------------------+--------------------------+--------------------+----------+------------------+---------+-

In [6]:
# Really ugly but what is the shape of hist
print('There are ',hist.count(),' rows in hist and ',len(hist.schema), ' columns')
print('The columns are \n')
hist.printSchema()

('There are ', 999937, ' rows in hist and ', 73, ' columns')
The columns are 

root
 |-- subscriberid: string (nullable = true)
 |-- privacy: string (nullable = true)
 |-- osSet: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- vzCategMap: map (nullable = true)
 |    |-- key: string
 |    |-- value: array (valueContainsNull = true)
 |    |    |-- element: string (containsNull = true)
 |-- appCategMap: map (nullable = true)
 |    |-- key: string
 |    |-- value: array (valueContainsNull = true)
 |    |    |-- element: string (containsNull = true)
 |-- dmaMap: map (nullable = true)
 |    |-- key: string
 |    |-- value: array (valueContainsNull = true)
 |    |    |-- element: string (containsNull = true)
 |-- stateMap: map (nullable = true)
 |    |-- key: string
 |    |-- value: array (valueContainsNull = true)
 |    |    |-- element: string (containsNull = true)
 |-- vzcategories: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- ap

In [6]:
hist.createOrReplaceTempView("table1")
df2 = spark.sql("SELECT Subscriberid, tldAggScores from table1") 
df2.na.drop(subset=["tldAggScores"]).show()

#hist_tld = df2.rdd
#print(hist_tld.map(lambda x:(x[1]))).\
 #   reduce(lambda x:type(x))
#import matplotlib.pyplot as plt


+----------------+--------------------+
|    Subscriberid|        tldAggScores|
+----------------+--------------------+
|1002918146000000|Map(glenbrookdodg...|
|1012055392000000|Map(usmilitarymus...|
|1015120891000000|Map(lindasecrist....|
|1018474139000000|Map(bcferries.com...|
|1018968166000000|Map(golfcollege.e...|
|1018993199000000|Map(cccti.edu -> ...|
|1019396984000000|Map(bryancountyga...|
|1027589075000000|Map(kfc.com.cn ->...|
|1033106947000000|Map(rlac.com -> 1...|
|1042983399000000|Map(chevytalk.org...|
|1045509101000000|Map(ocean.k12.wa....|
|1047718671000000|Map(townofkentct....|
|1054753490000000|Map(shadowtrader....|
|1055439953000000|Map(jamestownharl...|
|1055541953000000|Map(brainerdsport...|
|1057793389000000|Map(bigtopbouncer...|
|1058106449000000|Map(metigoshemini...|
|1058180278000000|Map(kasd.org -> 1.0)|
|1058502991000000|Map(metrotvnews.c...|
|1059717619000000|Map(marealtor.com...|
+----------------+--------------------+
only showing top 20 rows



In [9]:
from pyspark.sql.functions import explode
from pyspark.sql.functions import col

keys = (df2
    .select(explode("tldAggScores"))
    .select("key")
    .distinct()
    .rdd.flatMap(lambda x: x)
    .collect())

exprs = [col("tldAggScores").getItem(k).alias(k) for k in keys]
websites = df2.select(*exprs)


In [14]:
websites.toPandas()

Py4JJavaError: An error occurred while calling o526100.collectToPython.
: org.apache.spark.SparkException: Job 11 cancelled because SparkContext was shut down
	at org.apache.spark.scheduler.DAGScheduler$$anonfun$cleanUpAfterSchedulerStop$1.apply(DAGScheduler.scala:808)
	at org.apache.spark.scheduler.DAGScheduler$$anonfun$cleanUpAfterSchedulerStop$1.apply(DAGScheduler.scala:806)
	at scala.collection.mutable.HashSet.foreach(HashSet.scala:78)
	at org.apache.spark.scheduler.DAGScheduler.cleanUpAfterSchedulerStop(DAGScheduler.scala:806)
	at org.apache.spark.scheduler.DAGSchedulerEventProcessLoop.onStop(DAGScheduler.scala:1668)
	at org.apache.spark.util.EventLoop.stop(EventLoop.scala:83)
	at org.apache.spark.scheduler.DAGScheduler.stop(DAGScheduler.scala:1587)
	at org.apache.spark.SparkContext$$anonfun$stop$8.apply$mcV$sp(SparkContext.scala:1826)
	at org.apache.spark.util.Utils$.tryLogNonFatalError(Utils.scala:1283)
	at org.apache.spark.SparkContext.stop(SparkContext.scala:1825)
	at org.apac

----------------------------------------
Exception happened during processing of request from ('127.0.0.1', 35966)
----------------------------------------


Traceback (most recent call last):
  File "/usr/lib/python2.7/SocketServer.py", line 290, in _handle_request_noblock
    self.process_request(request, client_address)
  File "/usr/lib/python2.7/SocketServer.py", line 318, in process_request
    self.finish_request(request, client_address)
  File "/usr/lib/python2.7/SocketServer.py", line 331, in finish_request
    self.RequestHandlerClass(request, client_address, self)
  File "/usr/lib/python2.7/SocketServer.py", line 652, in __init__
    self.handle()
  File "/home/andrew/Downloads/spark-2.1.0-bin-hadoop2.7/python/pyspark/accumulators.py", line 235, in handle
    num_updates = read_int(self.rfile)
  File "/home/andrew/Downloads/spark-2.1.0-bin-hadoop2.7/python/pyspark/serializers.py", line 557, in read_int
    raise EOFError
EOFError


In [12]:
len(websites.schema)

websites["dteenergy.com"]
#colsums = websites.withColumn('total', sum(websites[col] for col in websites.columns))

AnalysisException: u'Cannot resolve column name "dteenergy.com" among (dteenergy.com, crpdsports.org, oakhillgolf.com, gymratsbasketball.com, bellscb.com, carlsbadseapointe.com, silvercupstudios.com, buds-harley.com, sgrho1922.org, woodfordreserve.com, bargainchildrensclothing.com, lakefrontlainey.com, orangecountyminingco.com, bistro821.com, energylogic.com, cabooselake.com, boydscoffeestore.com, korel.com, mrnussbaum.com, printpps.com, shootersofcolumbus.com, ideacenter.org, countrybank.com, fashionisers.com, oregonjamboree.com, chccw.org, my-thank-you-site.com, techmeme.com, assemblyoftrueisrael.com, smithfieldcity.org, bamboo.org, recordbuck.com, wings-fine-arts.com, powerpage.org, kevintomlinson.com, thompsonhine.com, toddlertoddler.com, delawarepark.com, sethkaller.com, fairfieldmemorial.org, mapesauction.com, astroford.com, spencerstuart.com, psychickelli.com, tysonfoods.com, daytonadodgechrysler.net, bigdweb.com, politicalmedia.com, ledwell.com, ringor.com, northerncontours.com

In [10]:
children = spark.sql("SELECT Subscriberid, child_in_hshld_count from table1") 
children.na.drop(subset=["child_in_hshld_count"]).count()

299768